In [ ]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

tokenizer = T5Tokenizer.from_pretrained("pretrained/molt5-large-smiles2caption", model_max_length=512)
model = T5ForConditionalGeneration.from_pretrained('pretrained/molt5-large-smiles2caption')

# input_texts = [
#     'Cn1ccc(CCC(=O)Nc2nc3c(s2)C[C@H](c2ccccc2)CC3)n1 is a compound containing a pyridine ring substituted at the nitrogen with a carbon chain leading to an amide linkage. The amide group connects to a thiazole ring fused with a cyclohexane ring. The thiazole ring has a chiral center with an (R)-configuration attached to a phenyl ring.',
#     'C[C@@H](C(=O)N1CCCO[C@@H](c2ccccc2)C1)c1ccc2c(c1)OCO2 is a compound featuring a benzodioxole ring fused with a benzene ring. Attached to this system is a chiral center with an (S)-configuration. The chiral center is part of an amide group linked to a morpholine ring that also has a chiral center with an (S)-configuration, connected to a phenyl ring.',
#     'COC[C@@H]1CN(C(=O)c2ccc(-c3ccc(C)c(C)c3)cc2F)C[C@@H](C)O1 is a molecule with a morpholine ring containing two chiral centers, both with (S)-configurations. It includes a methoxy group and an amide linkage attached to a fluorinated benzene ring. The benzene ring is further substituted with a biphenyl group where one phenyl ring has two methyl groups.',
#     'CC[C@@H](NC[C@@H]1CCN(S(=O)(=O)c2cccs2)C1)C1CCCCC1 is a compound with a piperidine ring containing two chiral centers, both with (S)-configurations. The piperidine ring is connected to a sulfonamide group attached to a thiophene ring. Additionally, the molecule has a cyclohexane ring and a short alkyl chain with an amine linkage.',
#     'COCCN(C(=O)NCc1cccc(CSC)c1)[C@H]1CC[C@H](C)C1 is a molecule featuring a piperidine ring with two chiral centers, both with (S)-configurations. It includes a methoxyethyl group and an amide linkage. The amide is connected to a benzene ring that has a thiomethyl substituent.'
#     'COc1ccc(CC(=O)Nc2cc3sc(C)nc3cc2OC)c(F)c1 is a compound with a benzene ring substituted with a fluorine atom and a methoxy group. The benzene ring is connected to a carbon chain leading to an amide linkage, which is further attached to a thiazole ring fused with a pyridine ring. The thiazole ring contains a methyl group substitution.',
#     'C[C@@H]1CN(C(=O)NC[C@@H](Cc2ccccc2)C(F)(F)F)C[C@@H](C)S1 is a molecule featuring a piperidine ring with three chiral centers, all in the (S)-configuration. It includes an amide linkage and a trifluoromethyl group. The piperidine ring is connected to a phenyl ring and a thioether group.',
#     'CC(C)Oc1cccc(CNC(=O)c2ccccc2Oc2cnn(C)c2)c1 is a compound with a benzene ring substituted with an isopropoxy group and connected to a carbon chain leading to an amide linkage. The amide is further connected to another benzene ring which is substituted with a methoxy group and a triazole ring.',
#     'O=C(COCc1ccccn1)NCC1(c2ccc(Cl)cc2)CCCC1 is a molecule with a piperidine ring fused with a cyclopentane ring. It includes a carbonyl group attached to an ether linkage, which is connected to a pyridine ring. The piperidine ring is also connected to a phenyl ring substituted with a chlorine atom.',
#     'C[C@@H]1CCC[C@@H](N(C)C(=O)C(=O)N[C@H](C)c2nc(C(C)(C)C)cs2)C1 is a compound with a piperidine ring containing two chiral centers, both in the (S)-configuration. It includes a tertiary amine and a diketone linkage. The piperidine ring is connected to a thiazole ring substituted with a tert-butyl group.',
#     ]
input_smiles = [
    'COc1ccc(CC(=O)Nc2cc3sc(C)nc3cc2OC)c(F)c1',
    'C[C@@H]1CN(C(=O)NC[C@@H](Cc2ccccc2)C(F)(F)F)C[C@@H](C)S1',
    'CC(C)Oc1cccc(CNC(=O)c2ccccc2Oc2cnn(C)c2)c1',
    'O=C(COCc1ccccn1)NCC1(c2ccc(Cl)cc2)CCCC1',
    'C[C@@H]1CCC[C@@H](N(C)C(=O)C(=O)N[C@H](C)c2nc(C(C)(C)C)cs2)C1',
]
input_texts = []
for smiles in input_smiles:
    input_ids = tokenizer(smiles, return_tensors="pt").input_ids
    outputs = model.generate(input_ids, num_beams=5, max_length=512)
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))
    input_texts.append(tokenizer.decode(outputs[0], skip_special_tokens=True))



In [ ]:
import pandas as pd
from rdkit import Chem
from rdkit.Chem import Draw
import matplotlib.pyplot as plt
import pdb

tokenizer = T5Tokenizer.from_pretrained("pretrained/molt5-large-caption2smiles", model_max_length=512)
model = T5ForConditionalGeneration.from_pretrained('pretrained/molt5-large-caption2smiles')

results = []

for idx, input_text in enumerate(input_texts):
    input_ids = tokenizer(input_text, return_tensors="pt").input_ids
    outputs = model.generate(input_ids, num_beams=5, max_length=512)
    result = tokenizer.decode(outputs[0], skip_special_tokens=True)
    results.append([result, input_smiles[idx]])
# target = input_text.split("is represented as ")[-1].split(", where")[0]
# target = 'C[C@H]1[C@H]([C@H]([C@@H]([C@@H](O1)O[C@@H]2[C@H](O[C@H]([C@@H]([C@H]2O[C@H]3[C@@H]([C@H]([C@H]([C@H](O3)CO)O)OS(=O)(=O)O)O)NC(=O)C)O)CO)O)O)O'
# target = 'C1=CC(=CC=C1/C=C/CC[C@H](CCC2=CC(=C(C=C2)O)O)O)O'
# target = 'C[C@@H]1CCN(C[C@@H]1N(C)C2=NC=NC3=C2C=CN3)C(=O)CC#N'

fig, axs = plt.subplots(len(results), 2, figsize=(20, len(results)*5))
for idx, pair in enumerate(results):
    result, target = pair[0], pair[1]
    # pdb.set_trace()
    result_mol = Chem.MolFromSmiles(result)
    result_img = Draw.MolToImage(result_mol)
    target_mol = Chem.MolFromSmiles(target)
    target_img = Draw.MolToImage(target_mol)

    axs[idx, 0].imshow(result_img)
    axs[idx, 0].axis("off")
    axs[idx, 0].set_title(f'{result[:len(target)*3]}')
    axs[idx, 1].imshow(target_img)
    axs[idx, 1].axis("off")
    axs[idx, 1].set_title(f'{target}')
plt.tight_layout()
plt.show()

In [2]:
import re
from rdkit import Chem
from rdkit.Chem import Draw
from rdkit.Chem import rdmolops
from rdkit.Chem import AllChem
import matplotlib.pyplot as plt

# def correct_benzene_rings(smiles):
#     mol = Chem.MolFromSmiles(smiles)
#     if mol is None:
#         return None
    
#     ring_info = mol.GetRingInfo()
#     atom_rings = ring_info.AtomRings()
    
#     for ring in atom_rings:
#         ring_atoms = [mol.GetAtomWithIdx(idx) for idx in ring]
#         bond_types = [bond.GetBondType() for bond in [mol.GetBondBetweenAtoms(ring[i], ring[(i + 1) % len(ring)]) for i in range(len(ring))]]
        
#         # 判断是否为不合理的环（例如，大环或多个双键环）
#         if len(ring) == 6 and bond_types.count(Chem.rdchem.BondType.DOUBLE) > 1:
#             # 将不合理的环替换为苯环结构
#             for atom in ring_atoms:
#                 atom.SetIsAromatic(True)
#             for bond in [mol.GetBondBetweenAtoms(ring[i], ring[(i + 1) % len(ring)]) for i in range(len(ring))]:
#                 bond.SetBondType(Chem.rdchem.BondType.AROMATIC)
#                 bond.SetIsAromatic(True)

    
#     # 对分子进行规范化和检查
#     try:
#         AllChem.SanitizeMol(mol)
#         return Chem.MolToSmiles(mol, kekuleSmiles=False)
#     except Exception as e:
#         print(f"Error sanitizing molecule: {e}")
#         return smiles

def correct_benzene_rings(smiles):
    try:
        mol = Chem.MolFromSmiles(smiles)
        if mol is None:
            return None
    
        ring_info = mol.GetRingInfo()
        atom_rings = ring_info.AtomRings()
    
        for ring in atom_rings:
            ring_atoms = [mol.GetAtomWithIdx(idx) for idx in ring]
            bond_types = [bond.GetBondType() for bond in [mol.GetBondBetweenAtoms(ring[i], ring[(i + 1) % len(ring)]) for i in range(len(ring))]]
        
            # 将不合理的环替换为苯环结构
            if len(ring) == 6 and bond_types.count(Chem.rdchem.BondType.DOUBLE) > 1:
                for bond in [mol.GetBondBetweenAtoms(ring[i], ring[(i + 1) % len(ring)]) for i in range(len(ring))]:
                    bond.SetBondType(Chem.rdchem.BondType.AROMATIC)
                    bond.SetIsAromatic(True)
                for atom in ring_atoms:
                    atom.SetIsAromatic(True)
    
        # 对分子进行规范化和检查
        try:
            AllChem.SanitizeMol(mol)
            return Chem.MolToSmiles(mol, kekuleSmiles=False)
        except Exception as e:
            print(smiles)
            # 检查环中每个原子的当前化合价
            for atom in mol.GetAtoms():
                current_valence = sum(bond.GetBondTypeAsDouble() for bond in atom.GetBonds())
                if current_valence > 4:
                    # 如果化合价超出，将所有双键转换为单键
                    for bond in mol.GetBonds():
                        if bond.GetBondType() == Chem.rdchem.BondType.DOUBLE:
                            bond.SetBondType(Chem.rdchem.BondType.SINGLE)
                            bond.SetIsAromatic(False)
            try:
                AllChem.SanitizeMol(mol)
                return Chem.MolToSmiles(mol, kekuleSmiles=False)
            except Exception as e:
                return "C"
            
    except Exception as e:
        print(f"Error!!! processing SMILES {smiles}: {e}")
        return smiles

# 示例SMILES列表
smiles_list = [
    "B([C@H](CC(C)C)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)C2=NC=CN=C2)(O)O",
    "CCOB(OC(C)O)C(NC(=O)CCC1=C=C=C=C=C1)C(OOC)C(C)C",
    "CC(CO)CC(NC(=O)CCC1=C=C(O)C=C=C1)B(O)O",
    "CCC1=C=C(CCC(=O)NC(B(O)O)C(O)C(C)C)C=C=C1",
    "CCC1(C)CC(C)CC(B2OCO2)NC(=O)CCC12C=C=CC(C)=C2",
    "CC(C)C1COOC(CCC2C=C=C=C=C2O)NC1B(O)OC=O",
    "CC=CC1=C(O)C(C)C(OO)C2NC(=O)CCC3=C=C(C=C=C3)C1(O)OB2O",
    "CC(C)CC1(N2OBO2)C2C3CC4CCC(CCC1(O)NN2O3)CC4BCl",
    "CC1CC=[N+](C(=O)CCC2=C=C=C=C=C2)C(B(O)O)C1C",
    "CC(COO)C(C)C(B(O)O)[NH+]1OC2=C=C=C=CC2CCC1=O",
    "C=CC(C(C)C)C(NC(O)(CC)CCC1(C)C=C=C=C=C1O)B(O)O",
    "C=[N+]1C(=O)CCC2(C=C=C=C=C2)OCCC(C)C(C)C1B(O)O",
    "CCOB(O)C1NC(=O)CCC2C=C=C=C=C2CCCC(C)C1OC",
    "CCCC1OC23C1C21C2C=CC1C3(CCl)C2CCC(O)NCC",
    "C=C(C)C(C(NC(=O)CCC1C=C=C=C=C1C)B(O)O)C(C)C(C)O",
    "CC(C)CC(NC(=O)CCC1=C=C(O)C=C=C1)B(O)O",
    "CC1=C2C(CC3=C=C(C=C=C3)CCC(=O)NC(B(O)O)C(C)C2C)C1",
    "C=[N+](C(=O)CCC1C=C=C=C=C1C)C(B(O)O)C(CO)C(C)C",
    "CC=C(C(C)CCCO)C(NC(=O)CCC1=C=C(C)C=C=C1)B(O)OC",
    "C=C=[N+](C(=O)CCC1C=C=C=C=C1C)C(B(O)O)C(C=O)C(C)C",
    "CCOB1OCOC(C)C2(C=C=C=C=C2)CCC(=O)NC1CC(C)C",
    "CC1(CO)CCC2=C=C=C=CC2CCC(=O)NC(B(O)O)C1",
    "CC1CC2(C)C(OOO)C12C(BO)NC(=O)CCC1=C=C(OCO)C=C=C1",
    "CC(C)CC(NC(=O)CCC1=C=C=C=C=C1)B(O)O",
    "CC(C)C(C)C(NC(=O)CCC1=C=C=C=C=C1)B(O)OF",
    "CC1CC2C1C(B(O)O)NC(OCO)CCC21C=C=C=C=C1",
    "C=C1OCC(C)C(CO)C(B(O)OO)NC(=O)CC1C1=C=C=C=C=C1",
    "CC1CC(C)OC(CCC2=C=C=C=C=C2)[N+]2=CC=COB(O)C2C1",
    "COB(OO)C(NC(=O)CCC1=C=C=C=C=C1)C(C(C)C)C(C)C",
    "CC(C)C1CC2CC3(C=C=C=C=C23)CCC(=O)NC1B(O)O",
    "COB(O)C1(C)CC(C)C(OC)=C(C)C2=C=C(C=C=C2)CCC(=O)N1",
    "CC(CNC(=O)CCC1=C=C=C=C=C1)C(C)C(=CO)COB(O)O",
    "CCC(C(C)CO)C1NC(=O)CCC2C=C=C=C=C2OOB1O",
    "CC(C)C(C)C1NC(=O)CCC2=C=C(C=C=C2)C=COB1O",
    "CCOB(O)C1CC(C)C2C3CC2(C)C(O)(CCC2C=C=C=C=C2O3)N1",
    "CC1CC2=C=C=C=CC2CCC(=O)NC(B(O)OOC=O)CC(C)C1",
    "C=C=[N+](C(=O)CCC1=C=C=C=C=C1)C(B(O)OOCC)C(CC)C(C)C",
    "CC1CC2C=CC1C(B(O)O)NC(=O)CCC21C=C=C=C=C1",
    "CC(C)CC(NC(=O)CCC1=C=C=C=C=C1)B(O)OO",
    "CC1=C=C=C=CC1CCC(=O)NC(CC(C)C)B(O)O",
    "CCOB(O)C(NC(CCC1C=C=C=C=C1C)OC=O)C1C(C)CC1(C)C",
    "C=C1C2(C=C=C=C=C2O)CCC(=O)NC(B(O)O)C1(O)C(C)CC",
    "CCC1(N)C(NOOCl)CC23CCCC(C2)N3C1C",
    "CC(C)CC(B1OC(C)O1)[NH+](C(=O)CCC1=C=C=C=C=C1)C(C)(C)C",
    "C=COB(O)C(CC(C)C)NC(=O)CCC1C=C=C=C=C1C",
    "CCC1C(C)C=COB(O)C1NC(=O)CCC1=C=C=C=C=C1",
    "CC1=CC2(C=C=C1)C1=C(C)CC3C(C)CCC2C(O)(C1)NC3B(O)O",
    "CCCC(CC)C(O)C(NC(CCC1=C=C(O)C=C=C1)OCC)B(O)OC",
    "CC=[N+]1C(=O)CC2=CC(CC3=C=C2C=C=C3)C2CC(C)C(C2)C1B(O)O",
    "COB1OC(C)(C)C2C(C)CC(O)C3=C=C(C=C=C3)CCC(=O)NC12",
    "CC1=CC(C)(CCC2OCCC(O)OB(O)C3C4C(C)CC4O[NH+]23)C=C=C1",
    "CCOOB(O)C(CC(C)CC)NC(=O)CCC1C=C=CC(C)=C1O",
    "C=C(C)C1=C=C(C2CC(=O)NC(CC(C)C)B(OC)OOCOO2)C=C=C1",
    "CC1C=CC1C(NC(=O)CCC1C=C=C=C=C1F)B1OC=CO1",
    "CC1OCOB2OCC13C2NC(=O)CC1=CC(C)(CC2=C=C=C=C=C21)C3C",
    "CCOB(O)C(NC(=O)CCC1C=C=C=C=C1C)C1CCCC1C",
    "CCC(C(C)C)C(B(O)O)[NH+](OC)C(=O)CCC1C=C=C=C=C1C",
    "CCOC1=COB(O)C(CC(C)CC)[NH+]1C(=O)CCC1=C=C=C=C=C1",
    "OC1C2OOCC(Cl)C3C14C1N2C12C31C=CCCC412",
    "CC(C)C(SO)C(B(O)O)[N+]1=CCOOC1CCC1=C=C=C=C=C1",
    "CC1=C=C(CCC(=O)NC2B(O)OCC=CC3(C)C=CC(C)C23O)C=C=C1",
    "CC1=COC(CCC2=C=C=C=C=C2)[NH+]1C(CC(C)C)B(O)O",
    "CCOC1CCC2=C=C(C=C=C2)CCC(C)CC(B2OCO2)[N+]1=O",
    "COCCC(C)CC(NC1CCC2C=C=C=C=C2OO1)B(O)OC",
    "CCOB(O)C(CC(C)CCO)NC(=O)CCC1=C=C(C)C=C=C1",
    "CCC1([OH2+])[NH2+]C2OC34OC3(OCl)C35C6CCCCC6C14C3CC(C)C25",
    "CBB1B(OBCl)OB2BB2BC2CCC1CC2",
    "CCC(C)C1C(B(O)O)NC(=O)CCC2C=C=C=C=C2CC1(C)O",
    "CC(C=O)C1=CC2=C=C(C=C=C2)CCC(=O)N2CCOB(O)C12C",
    "CCOB(O)C(NC(=O)CCC1=C=C(C)C=C=C1)C1OCC1C",
    "C=CC1=C=C=C=CC1CCC(NC(CC(C)CCC)B(O)O)OC",
    "C=C(CC(=O)NC(B(O)O)C(C)C(C)CO)C1C=C=C=C=C1O",
    "CBNOCC(BB1OBO1)CCCCCC",
    "CCOB(OCC)C(NC(=O)CCC1C=C=C=C=C1O)C(C)C(C)C",
    "C=CC1(NC(=O)CCC2=C=C=C=C=C2C)B(O)OO[SH](C)CC(C)C1CC",
    "CCC1=C=C=C=CC1CCC1NC(B(O)O)CC(C)C(CCOO)OO1",
    "CCC1=C=C(CCC(=O)NC(CC(C)COC)B(O)OC)C=C=C1",
    "CC=CC1C(CC)=C(O)C1C(NC(=O)CCC1=C=C=C=C=C1)B(O)O",
    "C=S(C)OB(O)C(CC(C)CC)NC(=O)CCC1C=C=C=C=C1C=O",
    "C=C(C)C(C)CC(NC(=O)CCC1=C=C(C)C=C=C1)B(O)OO",
    "CC1(Cl)CC2[O+]=C3CC4C5C6C=C7C8C=C6C6(CC(BOC72C416)N3)OC85",
    "C=CCOC(CCC1C=C=C=C=C1C)NC(CC(C)CO)B(O)OOC",
    "CC1CCC23CC12C(NC(=O)CCC1C2=C=C=C=C1C2)B(O)O3",
    "CCOB(O)C(NC(=O)CCC1C=C=C=C=C1C)C1CCC1C",
    "CCOB1OC2C3=C=C=C=C2C3CCC(O)(C(C)C)NC1C1CCC1C",
    "CCC(C)C(C)(CC=O)C(NC(=O)CCC1=C=C=C=C=C1O)B(O)O",
    "CC1=C=C(CCC(=O)NC2B(O)OC3OC3C2C(C)C)C=C=C1",
    "CC1CCC2(CCC3=C=C=C=C=C3O)OCCN2C(B(O)O)C1",
    "C=CC(C(C)C)C(NC(=O)CCC1(C(=CC)CO)C=C=C=C=C1)B(O)O",
    "CC1=C=C=C=C(CCC(OO)[N+]2=COC(C)C(C)CC2B(O)OO)C1",
    "COOC(CCC1C=C=C=C=C1OC)NC(CC(C)C)B(O)O",
    "CCOB1OCC2(C=C=C=C=C2O)CCC(=O)NC1C(OC)C(C)C",
    "C=[N+](C(=O)CCC1=C=C=C=C=C1)C(B(O)O)C(CCC)C(C)C",
    "CCC(C(C)C)C(NC(=O)CCC1=C=C=C=C=C1)(OC)B(O)O"
]

# smiles_list = [
#     "CC1(C)CC(C)CC(B2OCO2)NC(=O)CCC12C=C=CC(C)=C2",
#     "C=CC(C(C)C)C(NC(O)(CC)CCC1(C)C=C=C=C=C1O)B(O)O",
#     "C=[N+]1C(=O)CCC2(C=C=C=C=C2)OCCC(C)C(C)C1B(O)O",
#     "CCOB1OCOC(C)C2(C=C=C=C=C2)CCC(=O)NC1CC(C)C",
#     "CC1CC2C1C(B(O)O)NC(OCO)CCC21C=C=C=C=C1",
#     "CC(C)C1CC2CC3(C=C=C=C=C23)CCC(=O)NC1B(O)O",
#     "CC1CC2C=CC1C(B(O)O)NC(=O)CCC21C=C=C=C=C1",
#     "C=C1C2(C=C=C=C=C2O)CCC(=O)NC(B(O)O)C1(O)C(C)CC",
#     "CC1=CC2(C=C=C1)C1=C(C)CC3C(C)CCC2C(O)(C1)NC3B(O)O",
#     "CC1=CC(C)(CCC2OCCC(O)OB(O)C3C4C(C)CC4O[NH+]23)C=C=C1",
#     "C=CC(C(C)C)C(NC(=O)CCC1(C(=CC)CO)C=C=C=C=C1)B(O)O",
#     "CCOB1OCC2(C=C=C=C=C2O)CCC(=O)NC1C(OC)C(C)C"
# ]

# 修正后的SMILES列表
corrected_smiles_list = [correct_benzene_rings(smiles) for smiles in smiles_list]

fig, axs = plt.subplots(len(smiles_list), 2, figsize=(20, len(smiles_list)*5))
for idx, pair in enumerate(zip(corrected_smiles_list, smiles_list)):
    # print(idx)
    result, target = pair[0], pair[1]
    # pdb.set_trace()
    result_mol = Chem.MolFromSmiles(result)
    result_img = Draw.MolToImage(result_mol)
    target_mol = Chem.MolFromSmiles(target)
    target_img = Draw.MolToImage(target_mol)

    axs[idx, 0].imshow(result_img)
    axs[idx, 0].axis("off")
    axs[idx, 0].set_title(f'{result[:len(target)*3]}')
    axs[idx, 1].imshow(target_img)
    axs[idx, 1].axis("off")
    axs[idx, 1].set_title(f'{target}')
plt.tight_layout()
plt.show()


[07:18:32] Can't kekulize mol.  Unkekulized atoms: 19 20 21 22 24
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 16 17 18 19 20
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 7 8 9 10 11
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 10 11 12 13 14
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 17 18 19 20 21
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 8 9 10 11 12
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 17 18 19 20 21
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 3 4 5 6 7
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 1 2 4 5 6
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 1 2 24 25 26
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 18 19 20 21 22
[07:18:32] Can't kekulize mol.  Unkekulized atoms: 7 8 9 10 11


CCC1(C)CC(C)CC(B2OCO2)NC(=O)CCC12C=C=CC(C)=C2
C=CC(C(C)C)C(NC(O)(CC)CCC1(C)C=C=C=C=C1O)B(O)O
C=[N+]1C(=O)CCC2(C=C=C=C=C2)OCCC(C)C(C)C1B(O)O
CCOB1OCOC(C)C2(C=C=C=C=C2)CCC(=O)NC1CC(C)C
CC1CC2C1C(B(O)O)NC(OCO)CCC21C=C=C=C=C1
CC(C)C1CC2CC3(C=C=C=C=C23)CCC(=O)NC1B(O)O
CC1CC2C=CC1C(B(O)O)NC(=O)CCC21C=C=C=C=C1
C=C1C2(C=C=C=C=C2O)CCC(=O)NC(B(O)O)C1(O)C(C)CC
CC1=CC2(C=C=C1)C1=C(C)CC3C(C)CCC2C(O)(C1)NC3B(O)O
CC1=CC(C)(CCC2OCCC(O)OB(O)C3C4C(C)CC4O[NH+]23)C=C=C1
C=CC(C(C)C)C(NC(=O)CCC1(C(=CC)CO)C=C=C=C=C1)B(O)O
CCOB1OCC2(C=C=C=C=C2O)CCC(=O)NC1C(OC)C(C)C
